In [1]:
import AETransformation
import AEWMVFTS
import PreProcessing
from sklearn.metrics import mean_absolute_error
import math
from pyFTS.common import Util
import datetime
import statistics
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from keras.models import Model
from keras.layers import Dense, Input
from keras import regularizers
from sklearn.preprocessing import MinMaxScaler
import pyFTS
from pyFTS.benchmarks import Measures
import statistics
from pyFTS.common.Util import persist_obj, load_obj
from pyFTS.models.multivariate import common, variable, wmvfts
from pyFTS.partitioners import Grid
from pyFTS.common import Membership

2021-09-26 15:18:06.748329: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2021-09-26 15:18:06.748378: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [2]:
df = pd.read_csv('HomeC.csv')
data = df.drop(labels=['icon','summary','cloudCover', 'House overall [kW]', 'time'], axis=1)
data = data.loc[0: : 10]
data.reset_index(inplace=True)
data.pop('index')

/usr/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3441: DtypeWarning: Columns (0,27) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


0             0
1            10
2            20
3            30
4            40
          ...  
50387    503870
50388    503880
50389    503890
50390    503900
50391    503910
Name: index, Length: 50392, dtype: int64

In [3]:
data.dropna()

use [kW]  gen [kW]  Dishwasher [kW]  Furnace 1 [kW]  Furnace 2 [kW]  \
0      0.932833  0.003483         0.000033        0.020700        0.061917   
1      1.585083  0.003417         0.000050        0.022100        0.678733   
2      0.533817  0.003450         0.000000        0.020633        0.062967   
3      1.190950  0.003083         0.000217        0.387400        0.061883   
4      1.582083  0.003067         0.000050        0.022050        0.681717   
...         ...       ...              ...             ...             ...   
50386  1.621417  0.004183         0.000033        0.441950        0.645467   
50387  0.896250  0.004150         0.000233        0.496633        0.063000   
50388  1.311617  0.004167         0.000017        0.359167        0.645433   
50389  2.059367  0.003383         0.000033        0.153367        0.643300   
50390  1.522583  0.003200         0.000067        0.023033        0.627233   

       Home office [kW]  Fridge [kW]  Wine cellar [kW]  Garage door [kW]  \
0              0.442633     0.124150          0.006983          0.013083   
1              0.440200     0.121450          0.007433          0.013583   
2              0.270033     0.004950          0.007033          0.013117   
3              0.256867     0.004933          0.101783          0.012533   
4              0.242433     0.005550          0.122400          0.013550   
...                 ...          ...               ...               ...   
50386          0.041767     0.129317          0.008067          0.012883   
50387          0.042317     0.123800          0.007850          0.012433   
50388          0.041917     0.005133          0.008167          0.013083   
50389          0.042050     0.005117          0.008283          0.013267   
50390          0.041767     0.005283          0.008433          0.013533   

       Kitchen 12 [kW]  ...  temperature  humidity  visibility  \
0             0.000417  ...        36.14      0.62       10.00   
1             0.000350  ...        36.14      0.62       10.00   
2             0.000750  ...        36.14      0.62       10.00   
3             0.000700  ...        36.14      0.62       10.00   
4             0.000567  ...        36.14      0.62       10.00   
...                ...  ...          ...       ...         ...   
50386         0.000317  ...        35.12      0.86        8.74   
50387         0.000467  ...        35.12      0.86        8.74   
50388         0.000650  ...        35.12      0.86        8.74   
50389         0.000433  ...        35.12      0.86        8.74   
50390         0.000467  ...        35.12      0.86        8.74   

       apparentTemperature  pressure  windSpeed  windBearing  precipIntensity  \
0                    29.26   1016.91       9.18        282.0           0.0000   
1                    29.26   1016.91       9.18        282.0           0.0000   
2                    29.26   1016.91       9.18        282.0           0.0000   
3                    29.26   1016.91       9.18        282.0           0.0000   
4                    29.26   1016.91       9.18        282.0           0.0000   
...                    ...       ...        ...          ...              ...   
50386                29.45   1011.49       6.72        186.0           0.0101   
50387                29.45   1011.49       6.72        186.0           0.0101   
50388                29.45   1011.49       6.72        186.0           0.0101   
50389                29.45   1011.49       6.72        186.0           0.0101   
50390                29.45   1011.49       6.72        186.0           0.0101   

       dewPoint  precipProbability  
0         24.40               0.00  
1         24.40               0.00  
2         24.40               0.00  
3         24.40               0.00  
4         24.40               0.00  
...         ...                ...  
50386     31.27               0.51  
50387     31.27               0.51  
50388     31.27               0.51  
50389     31.27      

In [9]:
names = ['factor_1']

In [10]:
def sliding_window_AE(data,n_windows,train_size,dim,fs, names):
    ae_wmvfts = AEWMVFTS.AEWeightedMVFTS(n_dimensions = dim,n_part = fs,endogen_variable='use [kW]',names=names)
    
    result = {
         "window": [],
         "rmse": [],
         "mape": [],
         "smape": [],
         "mae": []
    }

    order = 1
    tam = len(data)
    n_windows = 30
    windows_length = math.floor(tam / n_windows)
    for ct, ttrain, ttest in Util.sliding_window(data, windows_length, 0.75, inc=1):
        if len(ttest) > 0:
        
            data_train = ttrain.loc[:,'use [kW]':'precipProbability']
            data_test = ttest.loc[:,'use [kW]':'precipProbability']
        
        
            print('-' * 20)
            print(f'training window {(ct)}')
            model, ae_reduced_train = ae_wmvfts.run_train_model(data=data_train, epochs=50, n_layers=2, neuron_per_layer=[50,dim], batch=40, opt='adagrad', act='softsign')
            forecast, forecast_self, ae_reduced_test = ae_wmvfts.run_test_model(model=model, data=data_test, epochs=50, n_layers=2,
                                                           neuron_per_layer=[50,dim], batch=40, opt='adagrad', act='aoftsign')
        
        #Teste e cálculo dos erros da previsão
        #appliance_test = ttest['Appliances_t+1'].values
        
        #Teste e cálculo dos erros da previsão - valor use  é Appliances o use Appliances_t+1 --> label igual por causa do model
            print("[{0: %H:%M:%S}]".format(datetime.datetime.now()) + f" getting statistics")
            rmse = Measures.rmse(ae_reduced_test['use [kW]'].values.tolist(),forecast)
            mape = Measures.mape(ae_reduced_test['use [kW]'].values.tolist(),forecast)
            smape = Measures.smape(ae_reduced_test['use [kW]'].values.tolist(),forecast)
        
            forecast = pd.DataFrame(forecast)
            forecast.fillna(forecast.mean(),inplace=True)
            forecast = np.array(forecast).reshape(-1)
            mae = mean_absolute_error(ae_reduced_test['use [kW]'].values.tolist(), forecast)
        
        # Grafico de comparação Original x Previsto para cada janela
        #fig, ax = plt.subplots(nrows=1, ncols=1, figsize=[15, 3])
        #ax.plot(pca_reduced_test['Appliances'], label='Original')
        #ax.plot(forecast, label='Forecast')
        #handles, labels = ax.get_legend_handles_labels()
        #lgd = ax.legend(handles, labels, loc=2, bbox_to_anchor=(1, 1))
        #plt.show()
        
            result["rmse"].append(rmse)
            result["mape"].append(mape)
            result["smape"].append(smape)
            result["mae"].append(mae)
            result["window"].append(ct)
        
            
    measures = pd.DataFrame(result)
    return measures

In [11]:
dimensions = [2,3,4,5,6]
fuzzy_sets = [10,20,30,40,50]

final_result = {
    "dimensions": [],
    "fuzzy_sets": [],
    "rmse": [],
    "mae": [],
    "mape": [],
    "smape": []
}

n_windows = 30
train_size = 0.75

for dim in dimensions:
    names.append('factor_'+str(dim))
    print (names)
    for fs in fuzzy_sets:
        measures = sliding_window_AE(data,n_windows,train_size,dim,fs, names)
        final_result["dimensions"].append(dim)
        final_result["fuzzy_sets"].append(fs)
        
        rmse = round(statistics.mean(measures['rmse']),3)
        mape = round(statistics.mean(measures['mape']),3)
        smape = round(statistics.mean(measures['smape']),3)
        mae = round(statistics.mean(measures['mae']),3)
        
        final_result["rmse"].append(rmse)
        final_result["mape"].append(mape)
        final_result["smape"].append(smape)
        final_result["mae"].append(mae)
        
        print(f'Results: {(dim,fs,rmse,mae,mape,smape)}')
        
        
final_measures_ae = pd.DataFrame(final_result) 

print("Statistics PCA-WMVFTS (test): ")
final_measures_ae

['factor_1', 'factor_2']
--------------------
training window 0
Epoch 1/50


/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


42/42 [==============================] - 1s 2ms/step - loss: 0.1527
Epoch 2/50
42/42 [==============================] - 0s 2ms/step - loss: 0.1315
Epoch 3/50
42/42 [==============================] - 0s 2ms/step - loss: 0.1090
Epoch 4/50
42/42 [==============================] - 0s 2ms/step - loss: 0.0837
Epoch 5/50
42/42 [==============================] - 0s 5ms/step - loss: 0.0628
Epoch 6/50
42/42 [==============================] - 0s 5ms/step - loss: 0.0511
Epoch 7/50
42/42 [==============================] - 0s 4ms/step - loss: 0.0458
Epoch 8/50
42/42 [==============================] - 0s 4ms/step - loss: 0.0432
Epoch 9/50
42/42 [==============================] - 0s 5ms/step - loss: 0.0419
Epoch 10/50
42/42 [==============================] - 0s 4ms/step - loss: 0.0411
Epoch 11/50
42/42 [==============================] - 0s 4ms/step - loss: 0.0404
Epoch 12/50
42/42 [==============================] - 0s 5ms/step - loss: 0.0399
Epoch 13/50
42/42 [==============================] - 0s 4ms/

/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


Epoch 1/50
14/14 [==============================] - 0s 2ms/step - loss: 0.1578
Epoch 2/50
14/14 [==============================] - 0s 2ms/step - loss: 0.1409
Epoch 3/50
14/14 [==============================] - 0s 2ms/step - loss: 0.1276
Epoch 4/50
14/14 [==============================] - 0s 2ms/step - loss: 0.1157
Epoch 5/50
14/14 [==============================] - 0s 2ms/step - loss: 0.1048
Epoch 6/50
14/14 [==============================] - 0s 2ms/step - loss: 0.0951
Epoch 7/50
14/14 [==============================] - 0s 2ms/step - loss: 0.0869
Epoch 8/50
14/14 [==============================] - 0s 2ms/step - loss: 0.0801
Epoch 9/50
14/14 [==============================] - 0s 2ms/step - loss: 0.0746
Epoch 10/50
14/14 [==============================] - 0s 2ms/step - loss: 0.0703
Epoch 11/50
14/14 [==============================] - 0s 4ms/step - loss: 0.0669
Epoch 12/50
14/14 [==============================] - 0s 4ms/step - loss: 0.0642
Epoch 13/50
14/14 [==============================

...

/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


42/42 [==============================] - 0s 1ms/step - loss: 0.1328
Epoch 2/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0716
Epoch 3/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0480
Epoch 4/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0414
Epoch 5/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0394
Epoch 6/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0382
Epoch 7/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0370
Epoch 8/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0359
Epoch 9/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0347
Epoch 10/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0335
Epoch 11/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0324
Epoch 12/50
42/42 [==============================] - 0s 1ms/step - loss: 0.0314
Epoch 13/50
42/42 [==============================] - 0s 1ms/

/home/luizf/.local/lib/python3.9/site-packages/sklearn/base.py:441: UserWarning: X does not have valid feature names, but MinMaxScaler was fitted with feature names
  warnings.warn(


Epoch 1/50
14/14 [==============================] - 0s 1ms/step - loss: 0.1555
Epoch 2/50
14/14 [==============================] - 0s 1ms/step - loss: 0.1289
Epoch 3/50
14/14 [==============================] - 0s 1ms/step - loss: 0.1101
Epoch 4/50
14/14 [==============================] - 0s 1ms/step - loss: 0.0946
Epoch 5/50
14/14 [==============================] - 0s 1ms/step - loss: 0.0815
Epoch 6/50
14/14 [==============================] - 0s 1ms/step - loss: 0.0715
Epoch 7/50
14/14 [==============================] - 0s 1ms/step - loss: 0.0645
Epoch 8/50
14/14 [==============================] - 0s 1ms/step - loss: 0.0598
Epoch 9/50
14/14 [==============================] - 0s 1ms/step - loss: 0.0567
Epoch 10/50
14/14 [==============================] - 0s 1ms/step - loss: 0.0546
Epoch 11/50
14/14 [==============================] - 0s 1ms/step - loss: 0.0531
Epoch 12/50
14/14 [==============================] - 0s 1ms/step - loss: 0.0519
Epoch 13/50
14/14 [==============================

dimensions  fuzzy_sets   rmse    mae    mape   smape
0            2          10  0.339  0.278  63.341  15.580
1            2          20  0.209  0.126  34.541   5.790
2            2          30  0.101  0.041  17.692   2.331
3            2          40  0.059  0.014   2.874   0.970
4            2          50  0.047  0.014   2.344   0.780
5            3          10  0.188  0.086  20.641   4.629
6            3          20  0.033  0.010   1.622   0.720
7            3          30  0.025  0.004   0.537   0.203
8            3          40  0.015  0.005   0.834   0.241
9            3          50  0.007  0.003   0.435   0.136
10           4          10  0.068  0.032   6.151   1.951
11           4          20  0.011  0.004   0.471   0.150
12           4          30  0.002  0.002   0.207   0.054
13           4          40  0.002  0.002   0.213   0.054
14           4          50  0.001  0.002   0.193   0.047
15           5          10  0.034  0.008   1.823   0.514
16           5          20  0.002  0.002   0.199   0.051
17           5          30  0.001  0.002   0.195   0.048
18           5          40  0.000  0.002   0.190   0.046
19           5          50  0.000  0.002   0.190   0.046
20           6          10  0.009  0.004   0.397   0.136
21           6          20  0.001  0.002   0.189   0.046
22           6          30  0.001  0.002   0.189   0.045
23           6          40  0.000  0.002   0.190   0.046
24           6          50  0.000  0.002   0.190   0.046

In [12]:
final_measures_ae.to_csv (r'ae_wmvfts_dim_fsets.csv', index = False, header=True)